In [1]:
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import json
import operator
with open('training/label.idl') as f:
    lines = f.read().splitlines()
    annotations = {}
    for line in lines:
        annotation = json.loads(line)
        annotations.update(annotation)
    annotation_list = {}    
    for k,v in annotations.items():
        bboxes = []
        for box in v:
            xmin, ymin, xmax, ymax,cls = box
            x1 = int(xmin) - 1
            y1 = int(ymin) - 1
            x2 = int(xmax) - 1
            y2 = int(ymax) - 1

            cx = (x2+x1)/2.
            cy = (y2+y1)/2
            w = x2-x1
            h = y2-y1
            bboxes.append([cx, cy, w, h, cls])
        annotation_list[k]=bboxes

In [2]:
i = 0
for k,v in annotation_list.items():
    i += 1
    print(k, annotations[k])
    print(k,v)
    if i == 1:
        break

(u'63526.jpg', [[119.49951999999999, 200.49984, 147.74976, 212.74992000000003, 1], [281.00032, 199.25028, 294.50048, 212.00004, 1]])
(u'63526.jpg', [[132.0, 205, 28, 12, 1], [286.5, 204, 13, 13, 1]])


In [5]:
import mxnet as mx
import numpy as np
import cv2


# get iterator
def get_iterator(path, data_shape, label_width, batch_size, shuffle=False):
    iterator = mx.io.ImageRecordIter(path_imgrec=path,
                                    data_shape=data_shape,
                                    label_width=label_width,
                                    batch_size=batch_size,
                                    shuffle=shuffle)
    return iterator


# Convert data to rec file
def get_YOLO_xy(bxy, grid_size=(7,7), dscale=32, sizet=224):
    cx, cy = bxy
    assert cx<=1 and cy<=1, "All should be < 1, but get {}, and {}".format(cx,cy)

    j = int(np.floor(cx/(1.0/grid_size[0])))
    i = int(np.floor(cy/(1.0/grid_size[1])))
    xyolo = (cx * sizet - j * dscale) / dscale
    yyolo = (cy * sizet - i * dscale) / dscale
    return [i, j, xyolo, yyolo]


# Get YOLO label
def imgResizeBBoxTransform(img, bbox, sizet, grid_size=(7,7,9), dscale=32):

    himg, wimg = img.shape[:2]
    imgR = cv2.resize(img, dsize=(sizet, sizet))
    bboxyolo = np.zeros(grid_size)
    for eachbox in bbox:
        cx, cy, w, h, cls = eachbox
        cxt = 1.0*cx/wimg
        cyt = 1.0*cy/himg
        wt = 1.0*w/wimg
        ht = 1.0*h/himg
        CLASSES = {1: [1, 0, 0, 0], 2: [0,1,0,0],3:[0, 0, 1, 0], 20: [0, 0, 0, 1]}
        
        assert wt<1 and ht<1
        i, j, xyolo, yyolo = get_YOLO_xy([cxt, cyt], grid_size, dscale, sizet)
        print "one yolo box is {}".format((i, j, xyolo, yyolo, wt, ht, CLASSES[cls]))
        label_vec = np.asarray([1, xyolo, yyolo, wt, ht] + CLASSES[cls])
        bboxyolo[i, j, :] = label_vec
    return imgR, bboxyolo


# Convert raw images to rec files
def toRecFile(imgroot, imglist, annotation, sizet, grid_size, dscale, name):

    record = mx.recordio.MXIndexedRecordIO(name + ".idx",
                                           name + ".rec", 'w')
    for i in range(len(imglist)):
        imgname = imglist[i]
        img = cv2.imread(imgroot+imgname)
        bbox = annotation[imgname]
        print "Now is processing img {}".format(imgname)
        imgR, bboxR = imgResizeBBoxTransform(img, bbox, sizet, grid_size, dscale)
        header = mx.recordio.IRHeader(flag=0, label=bboxR.flatten(), id=0, id2=0)
        s = mx.recordio.pack_img(header, imgR, quality=100, img_fmt='.jpg')
        record.write_idx(i, s)
    print "JPG to rec is Done"
    record.close()

if __name__ == "__main__":
    # transform jpg to rec file
    imgroot = "./training/"
    imglist = annotation_list.keys()
    sizet = 224
    training_size = int(len(imglist)*.5)
    toRecFile(imgroot, imglist[:training_size], annotation_list, sizet, (7,7,9), 32, 'train')
    toRecFile(imgroot, imglist[training_size:], annotation_list, sizet, (7,7,9), 32, 'val')

Now is processing img 63526.jpg
one yolo box is (3, 1, 0.44374999999999987, 0.9861111111111107, 0.04375, 0.03333333333333333, [1, 0, 0, 0])
one yolo box is (3, 3, 0.13359374999999973, 0.9666666666666668, 0.0203125, 0.03611111111111111, [1, 0, 0, 0])
Now is processing img 67777.jpg
one yolo box is (2, 0, 0.42109375, 0.411111111111111, 0.1234375, 0.14722222222222223, [1, 0, 0, 0])
one yolo box is (1, 1, 0.7171874999999999, 0.7694444444444444, 0.13125, 0.19166666666666668, [1, 0, 0, 0])
one yolo box is (2, 1, 0.5203125, 0.15833333333333321, 0.16875, 0.19444444444444445, [1, 0, 0, 0])
one yolo box is (2, 2, 0.49921875000000027, 0.838888888888889, 0.2140625, 0.2833333333333333, [1, 0, 0, 0])
one yolo box is (2, 2, 0.8546875000000003, 0.17777777777777803, 0.078125, 0.1111111111111111, [1, 0, 0, 0])
one yolo box is (2, 3, 0.5984374999999997, 0.411111111111111, 0.14375, 0.19444444444444445, [1, 0, 0, 0])
one yolo box is (2, 4, 0.030468749999999822, 0.04166666666666696, 0.0859375, 0.125, [1, 0,

Now is processing img 68445.jpg
one yolo box is (2, 5, 0.6000000000000005, 0.916666666666667, 0.384375, 0.41944444444444445, [1, 0, 0, 0])
one yolo box is (2, 4, 0.01953125, 0.8000000000000003, 0.1546875, 0.16944444444444445, [1, 0, 0, 0])
one yolo box is (2, 3, 0.5109375000000003, 0.7416666666666667, 0.084375, 0.10277777777777777, [1, 0, 0, 0])
one yolo box is (3, 1, 0.9468750000000001, 0.4805555555555556, 0.31875, 0.49722222222222223, [1, 0, 0, 0])
one yolo box is (3, 0, 0.5085937500000001, 0.5583333333333331, 0.1484375, 0.22777777777777777, [1, 0, 0, 0])
one yolo box is (2, 2, 0.8328124999999997, 0.411111111111111, 0.1, 0.19444444444444445, [1, 0, 0, 0])
Now is processing img 60992.jpg
one yolo box is (2, 1, 0.8757812499999997, 0.7611111111111111, 0.2828125, 0.5638888888888889, [1, 0, 0, 0])
one yolo box is (3, 0, 0.36093749999999997, 0.4805555555555556, 0.10625, 0.2, [1, 0, 0, 0])
Now is processing img 62656.jpg
one yolo box is (3, 5, 0.22265625, 0.20833333333333304, 0.1484375, 0.1

Now is processing img 61729.jpg
one yolo box is (5, 6, 0.026562499999999822, 0.016666666666666607, 0.26875, 0.5083333333333333, [1, 0, 0, 0])
one yolo box is (4, 3, 0.8882812499999995, 0.5694444444444446, 0.0484375, 0.05555555555555555, [1, 0, 0, 0])
one yolo box is (4, 3, 0.4398437500000001, 0.5499999999999998, 0.0421875, 0.06388888888888888, [1, 0, 0, 0])
one yolo box is (4, 3, 0.06796874999999991, 0.47222222222222143, 0.0453125, 0.08888888888888889, [1, 0, 0, 0])
Now is processing img 65046.jpg
one yolo box is (4, 5, 0.07500000000000018, 0.23888888888888893, 0.059375, 0.14166666666666666, [0, 0, 1, 0])
one yolo box is (3, 1, 0.8539062499999999, 0.9861111111111107, 0.0828125, 0.08888888888888889, [1, 0, 0, 0])
one yolo box is (4, 0, 0.8585937499999999, 0.8611111111111107, 0.2484375, 0.5861111111111111, [1, 0, 0, 0])
one yolo box is (4, 4, 0.06875000000000053, 0.10277777777777786, 0.028125, 0.11388888888888889, [0, 1, 0, 0])
one yolo box is (4, 3, 0.47265625, 0.12222222222222268, 0.05

Now is processing img 67474.jpg
one yolo box is (4, 2, 0.296875, 0.7250000000000005, 0.096875, 0.1361111111111111, [1, 0, 0, 0])
one yolo box is (4, 2, 0.87109375, 0.5888888888888886, 0.0546875, 0.07222222222222222, [1, 0, 0, 0])
one yolo box is (4, 3, 0.10078125000000027, 0.5111111111111111, 0.0390625, 0.06666666666666667, [1, 0, 0, 0])
one yolo box is (4, 4, 0.45156250000000053, 0.10277777777777786, 0.203125, 0.23333333333333334, [1, 0, 0, 0])
one yolo box is (4, 4, 0.07968749999999947, 0.6861111111111109, 0.16875, 0.225, [1, 0, 0, 0])
one yolo box is (4, 3, 0.6640625, 0.5499999999999998, 0.06875, 0.10833333333333334, [1, 0, 0, 0])
Now is processing img 68486.jpg
one yolo box is (4, 2, 0.734375, 0.08333333333333393, 0.41875, 0.35555555555555557, [1, 0, 0, 0])
one yolo box is (3, 0, 0.55234375, 0.6166666666666671, 0.1046875, 0.10555555555555556, [1, 0, 0, 0])
one yolo box is (1, 5, 0.22265625, 0.06944444444444464, 0.0359375, 0.1361111111111111, [0, 0, 0, 1])
one yolo box is (4, 5, 0.7

Now is processing img 61941.jpg
one yolo box is (5, 5, 0.9828125000000005, 0.13333333333333286, 0.28125, 0.4, [1, 0, 0, 0])
one yolo box is (4, 4, 0.15078125000000053, 0.5694444444444446, 0.0953125, 0.14444444444444443, [1, 0, 0, 0])
one yolo box is (4, 4, 0.73046875, 0.802777777777778, 0.1734375, 0.21666666666666667, [1, 0, 0, 0])
one yolo box is (3, 3, 0.08984375, 0.8111111111111109, 0.0078125, 0.027777777777777776, [0, 0, 0, 1])
one yolo box is (5, 3, 0.07343750000000027, 0.38611111111111107, 0.271875, 0.36666666666666664, [1, 0, 0, 0])
one yolo box is (4, 1, 0.99609375, 0.7055555555555557, 0.1140625, 0.13055555555555556, [1, 0, 0, 0])
one yolo box is (4, 1, 0.29062500000000013, 0.5888888888888886, 0.09375, 0.10555555555555556, [1, 0, 0, 0])
one yolo box is (5, 0, 0.7546875000000001, 0.26944444444444393, 0.215625, 0.325, [1, 0, 0, 0])
Now is processing img 63603.jpg
one yolo box is (2, 2, 0.9312499999999999, 0.9944444444444445, 0.115625, 0.18611111111111112, [1, 0, 0, 0])
one yolo b

...

Now is processing img 69577.jpg
one yolo box is (2, 5, 0.07500000000000018, 0.022222222222222143, 0.025, 0.1, [0, 0, 1, 0])
one yolo box is (2, 4, 0.13437499999999947, 0.17777777777777803, 0.078125, 0.10277777777777777, [1, 0, 0, 0])
one yolo box is (1, 3, 0.6859375000000005, 0.8861111111111111, 0.03125, 0.07777777777777778, [1, 0, 0, 0])
one yolo box is (2, 3, 0.9703124999999995, 0.04166666666666696, 0.0375, 0.05555555555555555, [1, 0, 0, 0])
one yolo box is (1, 3, 0.8062499999999995, 0.9444444444444446, 0.021875, 0.03611111111111111, [1, 0, 0, 0])
one yolo box is (1, 3, 0.42890625000000027, 0.9833333333333334, 0.0234375, 0.05, [1, 0, 0, 0])
Now is processing img 69144.jpg
one yolo box is (4, 6, 0.004687500000000178, 0.005555555555555536, 0.271875, 0.33055555555555555, [1, 0, 0, 0])
one yolo box is (3, 4, 0.375, 0.3833333333333333, 0.04375, 0.06944444444444445, [1, 0, 0, 0])
one yolo box is (3, 3, 0.5382812500000003, 0.9666666666666668, 0.1703125, 0.2722222222222222, [1, 0, 0, 0])
one

Now is processing img 68741.jpg
one yolo box is (4, 4, 0.9929687500000002, 0.08333333333333393, 0.4421875, 0.49166666666666664, [1, 0, 0, 0])
one yolo box is (3, 3, 0.6585937500000005, 0.6944444444444446, 0.1390625, 0.225, [1, 0, 0, 0])
one yolo box is (3, 3, 0.25390625, 0.5583333333333331, 0.0609375, 0.10555555555555556, [1, 0, 0, 0])
one yolo box is (3, 2, 0.6687499999999997, 0.6361111111111115, 0.0875, 0.13055555555555556, [1, 0, 0, 0])
one yolo box is (3, 2, 0.1656249999999999, 0.32499999999999973, 0.059375, 0.13055555555555556, [1, 0, 0, 0])
one yolo box is (3, 1, 0.73359375, 0.6361111111111115, 0.1015625, 0.15833333333333333, [1, 0, 0, 0])
one yolo box is (3, 1, 0.12656250000000013, 0.8694444444444445, 0.203125, 0.2222222222222222, [1, 0, 0, 0])
one yolo box is (4, 0, 0.546875, 0.47222222222222143, 0.15625, 0.5, [1, 0, 0, 0])
one yolo box is (3, 3, 0.1171875, 0.5194444444444444, 0.05625, 0.1111111111111111, [1, 0, 0, 0])
one yolo box is (3, 2, 0.5648437500000001, 0.59722222222222

Now is processing img 69336.jpg
one yolo box is (4, 3, 0.4453125, 0.822222222222222, 0.265625, 0.3888888888888889, [1, 0, 0, 0])
one yolo box is (4, 2, 0.1929687499999999, 0.20000000000000018, 0.1109375, 0.175, [1, 0, 0, 0])
one yolo box is (4, 1, 0.8210937499999997, 0.20000000000000018, 0.0734375, 0.1111111111111111, [1, 0, 0, 0])
one yolo box is (3, 0, 0.70546875, 0.6750000000000003, 0.2046875, 0.5, [1, 0, 0, 0])
one yolo box is (4, 2, 0.4609375, 0.18055555555555536, 0.06875, 0.09722222222222222, [1, 0, 0, 0])
Now is processing img 69417.jpg
one yolo box is (4, 2, 0.5648437500000001, 0.6666666666666661, 0.0609375, 0.1, [1, 0, 0, 0])
one yolo box is (4, 2, 0.8874999999999997, 0.6666666666666661, 0.034375, 0.05555555555555555, [1, 0, 0, 0])
one yolo box is (4, 3, 0.85546875, 0.1416666666666666, 0.1671875, 0.2611111111111111, [1, 0, 0, 0])
one yolo box is (4, 2, 0.2421875, 0.6861111111111109, 0.034375, 0.044444444444444446, [1, 0, 0, 0])
Now is processing img 61681.jpg
one yolo box is (

Now is processing img 69261.jpg
one yolo box is (2, 0, 0.48125000000000007, 0.9944444444444445, 0.140625, 0.6138888888888889, [1, 0, 0, 0])
one yolo box is (3, 1, 0.12109375, 0.033333333333333215, 0.1203125, 0.14166666666666666, [1, 0, 0, 0])
one yolo box is (3, 2, 0.28046875000000027, 0.09166666666666679, 0.1015625, 0.15, [1, 0, 0, 0])
one yolo box is (3, 2, 0.6687499999999997, 0.36388888888888893, 0.103125, 0.30277777777777776, [0, 0, 1, 0])
one yolo box is (3, 6, 0.2726562499999998, 0.5583333333333331, 0.1859375, 0.5333333333333333, [0, 0, 1, 0])
one yolo box is (3, 5, 0.6984374999999998, 0.13055555555555554, 0.040625, 0.19722222222222222, [0, 1, 0, 0])
one yolo box is (3, 4, 0.06328125000000018, 0.13055555555555554, 0.0546875, 0.21388888888888888, [0, 0, 1, 0])
one yolo box is (2, 3, 0.6804687499999997, 0.9361111111111113, 0.0234375, 0.10277777777777777, [0, 1, 0, 0])
one yolo box is (2, 3, 0.5437499999999997, 0.9361111111111113, 0.01875, 0.09444444444444444, [0, 1, 0, 0])
one yolo

Now is processing img 60250.jpg
one yolo box is (4, 2, 0.17656249999999973, 0.25833333333333286, 0.1625, 0.18055555555555555, [1, 0, 0, 0])
one yolo box is (4, 4, 0.20000000000000018, 0.0638888888888891, 0.04375, 0.06666666666666667, [1, 0, 0, 0])
one yolo box is (4, 3, 0.4234374999999999, 0.08333333333333393, 0.04375, 0.06666666666666667, [1, 0, 0, 0])
one yolo box is (4, 0, 0.8093750000000001, 0.6277777777777773, 0.234375, 0.46111111111111114, [1, 0, 0, 0])
one yolo box is (3, 2, 0.7671874999999999, 0.947222222222222, 0.059375, 0.10833333333333334, [1, 0, 0, 0])
one yolo box is (3, 3, 0.12812500000000027, 0.8694444444444445, 0.03125, 0.06111111111111111, [1, 0, 0, 0])
one yolo box is (4, 2, 0.6578124999999999, 0.08333333333333393, 0.075, 0.10833333333333334, [1, 0, 0, 0])
Now is processing img 62008.jpg
one yolo box is (3, 2, 0.7015625000000001, 0.07222222222222197, 0.0125, 0.016666666666666666, [0, 0, 0, 1])
one yolo box is (3, 3, 0.40703124999999973, 0.07222222222222197, 0.0109375,

In [ ]:
import cv2
img = cv2.imread('./training/63526.jpg')

In [ ]:
himg, wimg = img.shape[:2]

In [ ]:
wimg